<a href="https://colab.research.google.com/github/zbransi/solar_moving_magnetic_features/blob/main/calc_drifts_with_squeeze.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
%pip install reproject
%pip install sunpy[map]

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 30.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 195.2/195.2 kB 17.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 378.9/378.9 kB 30.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 276.4/276.4 kB 21.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.8/8.8 MB 75.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 53.5/53.5 kB 4.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.5/3.5 MB 58.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.4/44.4 kB 1.5 MB/s eta 0:00:00


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
from datetime import datetime, timedelta
from astropy.io import fits
from sunpy.map import Map, MapSequence
import sunpy.map
from matplotlib.backends.backend_pdf import PdfPages
from reproject import reproject_interp
from copy import copy
import matplotlib.pyplot as plt
import numpy as np
from astropy.coordinates import Angle
import astropy.units as u
import pandas as pd
from scipy.ndimage import zoom
from copy import deepcopy

In [ ]:
# method for cropping 33 pixels from the top
def crop(m):
    ny, nx = m.data.shape
    bl_px = (0, 0) * u.pixel
    tr_px = (nx - 1, ny - 34) * u.pixel

    bl_wd = m.pixel_to_world(*bl_px)
    tr_wd = m.pixel_to_world(*tr_px)

    nmap = m.submap(bottom_left=bl_wd, top_right=tr_wd)
    return nmap

# shift the axes to align them
def shift_wcs(m, x_arcsec_offset=0, y_arcsec_offset=0):
    new_meta = copy(m.meta)
    new_meta['CRVAL1'] -= x_arcsec_offset
    new_meta['CRVAL2'] -= y_arcsec_offset
    return Map(m.data, new_meta)

# apply a new set of axes to a layer
def apply_wcs(layer, applier):
    new_meta = layer.meta.copy()
    # these are all the keys for values that have to do with the axes
    # crval is center value, cdelt is arcsec/pixel, crpix is center pixel, crota is rotation angle, and ctype is unit
    for key in ['CRVAL1', 'CRVAL2', 'CDELT1', 'CDELT2', 'CRPIX1', 'CRPIX2', 'CROTA1', 'CROTA2', 'CTYPE1', 'CTYPE2']:
        if key in applier.meta:
            new_meta[key] = applier.meta[key]
    return Map(layer.data, new_meta)

In [ ]:
# load in iris files
sji2832 = fits.open("/content/drive/MyDrive/DATA_LM/iris_l2_20170915_230442_3624258055_SJI_2832_t000.fits")
MAPSEQ_2832 = MapSequence([Map(frame, sji2832[0].header) for frame in sji2832[0].data])
sji2832.close()

# add in time meta using datetime objects
obs_time = datetime.strptime(sji2832[0].header['DATE_OBS'], '%Y-%m-%dT%H:%M:%S.%f')
time_stamps = [obs_time + timedelta(seconds=sji2832[0].header['CDELT3'] * frame) for frame in range(len(sji2832[0].data))]
if (len(MAPSEQ_2832) == len(time_stamps)):
    for frame in range(len(MAPSEQ_2832)):
        MAPSEQ_2832[frame].meta['DATE_OBS'] = time_stamps[frame].strftime('%Y-%m-%dT%H:%M:%S.%f')

# with open('iris_date_obs.text', 'w') as f:
    # for dt in time_stamps:
        # f.write(dt.isoformat(timespec='milliseconds') + '\n')

In [ ]:
# load in hinode data
sotcont = fits.open("/content/drive/MyDrive/DATA_LM/SPcubes_20170915_224806_conti_index.fits")
for frame in range(1, len(sotcont)):
    sotcont[frame].header['CUNIT1'], sotcont[frame].header['CUNIT2'] = 'arcsec', 'arcsec' # change because it was stored as 'arcsecs'
MAPSEQ_CONT = MapSequence([Map(sotcont[frame].data, sotcont[frame].header) for frame in range(1, len(sotcont))])
sotcont.close()

# create new array that aligns by time
iris_times = [datetime.strptime(frame.meta['DATE_OBS'], '%Y-%m-%dT%H:%M:%S.%f') for frame in MAPSEQ_2832]
hinode_times = [datetime.strptime(frame.meta['DATE_OBS'], '%d-%b-%Y %H:%M:%S.%f') for frame in MAPSEQ_CONT]

match_hinode = []

for each_iris in iris_times:
    time_diff = [abs(each_hinode - each_iris) for each_hinode in hinode_times]
    match_hinode.append(crop(MAPSEQ_CONT[time_diff.index(min(time_diff))]))

MAPSEQ_CONT_ALIG = MapSequence(match_hinode)

# with open('hinode_date_obs.text', 'w') as f:
    # for m in MAPSEQ_CONT_ALIG.maps:
        # dt = datetime.strptime(m.meta['DATE_OBS'], '%d-%b-%Y %H:%M:%S.%f')
        # f.write(dt.isoformat(timespec='milliseconds') + '\n')

INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs



INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]


INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs



INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]


INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs



...

INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]


INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs



INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]


INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs



INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]


In [ ]:
# list of indices where the frame of hinode actually changes to NEW content
unique_indices = []
ct = MAPSEQ_CONT_ALIG[0].meta['DATE_OBS']
unique_indices.append(0)
for i, m in enumerate(MAPSEQ_CONT_ALIG):
    if m.meta['DATE_OBS'] != ct:
        unique_indices.append(i)
        ct = m.meta['DATE_OBS']

In [ ]:
def squeeze(ms):
    maplist = []
    for m in ms:
        original_data = m.data
        zoom_y = 354/352
        zoom_x = 116/120

        new_meta = deepcopy(m.meta)
        new_meta['CDELT1'] = m.meta['CDELT1'] / zoom_x
        new_meta['CDELT2'] = m.meta['CDELT2'] / zoom_y

        new_data = zoom(original_data, (zoom_y, zoom_x), order=3)
        maplist.append(Map(new_data, new_meta))
    return MapSequence(maplist)

In [ ]:
# coalign the map sequences
TRANSFORMS = []

def aim_ms(ms1, ms2):
    ls = []
    frame = -1
    df = pd.read_csv('/content/drive/MyDrive/DATA_LM/best_frame.csv', header=None)

    for i, (m1, m2) in enumerate(zip(ms1, ms2)):
        x_arcsec_offset = m2.meta['CRVAL1'] - m1.meta['CRVAL1']
        y_arcsec_offset = m2.meta['CRVAL2'] - m1.meta['CRVAL2']
        if i in unique_indices:
            frame += 1
        driftx = df.iloc[frame].iloc[1] * m2.meta['CDELT1']
        drifty = df.iloc[frame].iloc[2] * m2.meta['CDELT2']
        TRANSFORMS.append([x_arcsec_offset+driftx, y_arcsec_offset+drifty])
        shift_map = shift_wcs(m2, x_arcsec_offset=TRANSFORMS[i][0], y_arcsec_offset=TRANSFORMS[i][1])

        rpj, _ = reproject_interp(shift_map, m1.wcs, shape_out=m1.data.shape)
        fin_map = Map(rpj, shift_map.meta)
        ls.append(apply_wcs(fin_map, m1))

    return MapSequence(ls)

In [ ]:
# coalign two individual maps with a custom drift (for testing)
def aim_m(m1, m2, driftx=0, drifty=0):
    x_offset = m2.meta['CRVAL1'] - m1.meta['CRVAL1']
    y_offset = m2.meta['CRVAL2'] - m1.meta['CRVAL2']
    shift_map = shift_wcs(m2, x_arcsec_offset=x_offset, y_arcsec_offset=y_offset)
    shift_2_map = shift_wcs(shift_map, x_arcsec_offset=driftx, y_arcsec_offset=drifty)

    rpj, _ = reproject_interp(shift_2_map, m1.wcs, shape_out=m1.data.shape)
    fin_map = Map(rpj, shift_2_map.meta)
    return apply_wcs(fin_map, m1)

In [ ]:
def make_movie(mapseq, name):
    plt.figure()
    ani = mapseq.plot()
    ani.save(f"gifs/{name}.gif")

In [ ]:
MAPSEQ_2832_SQUEEZE = squeeze(MAPSEQ_2832)
MAPSEQ_2832_ALIG = aim_ms(MAPSEQ_CONT_ALIG[:], MAPSEQ_2832_SQUEEZE[:])

INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs

INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,crlt_obs



INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]
INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]


INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs

INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,crlt_obs



INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]
INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]


INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs

INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,crlt_obs



...

INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]
INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]


INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs

INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,crlt_obs



INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]
INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]


INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs

INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,crlt_obs



INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]
INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]


In [ ]:
# load in new iris files
def load_iris(t):
    sji = fits.open(f"/content/drive/MyDrive/DATA_LM/iris_l2_20170915_230442_3624258055_SJI_{t}_t000.fits")
    d = sji[0].data
    h = sji[0].header
    map_ls = [sunpy.map.Map(frame, h) for frame in d]
    map_seq = sunpy.map.MapSequence(map_ls)
    sji.close()

    obs_time = datetime.strptime(h['DATE_OBS'], '%Y-%m-%dT%H:%M:%S.%f')
    time_stamps = [obs_time + timedelta(seconds=h['CDELT3'] * frame) for frame in range(len(d))] # CDELT3 is the time interval between frames
    if (len(map_seq) == len(time_stamps)):
        for frame in range(len(map_seq)):
            map_seq[frame].meta['DATE_OBS'] = time_stamps[frame].strftime('%Y-%m-%dT%H:%M:%S.%f')

    return map_seq

In [ ]:
MAPSEQ_2796 = load_iris("2796")
MAPSEQ_1330 = load_iris("1330")
MAPSEQ_1400 = load_iris("1400")

In [ ]:
# apply coalignment to iris files
def aim_iris(ms1, ms2):
    ls = []

    for i, (m1, m2) in enumerate(zip(ms1, ms2)):
        shift_map = shift_wcs(m2, x_arcsec_offset=TRANSFORMS[i][0], y_arcsec_offset=TRANSFORMS[i][1])
        rpj, _ = reproject_interp(shift_map, m1.wcs, shape_out=m1.data.shape)
        fin_map = Map(rpj, shift_map.meta)
        ls.append(apply_wcs(fin_map, m1))

    return MapSequence(ls)

In [ ]:
MAPSEQ_2796_SQUEEZE = squeeze(MAPSEQ_2796)
MAPSEQ_2796_ALIG = aim_iris(MAPSEQ_CONT_ALIG, MAPSEQ_2796_SQUEEZE)
MAPSEQ_1330_SQUEEZE = squeeze(MAPSEQ_1330)
MAPSEQ_1330_ALIG = aim_iris(MAPSEQ_CONT_ALIG, MAPSEQ_1330_SQUEEZE)
MAPSEQ_1400_SQUEEZE = squeeze(MAPSEQ_1400)
MAPSEQ_1400_ALIG = aim_iris(MAPSEQ_CONT_ALIG, MAPSEQ_1400_SQUEEZE)

INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,crlt_obs



INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]


INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,crlt_obs



INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]


INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,crlt_obs



...

INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]


INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,crlt_obs



INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]


INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,crlt_obs



INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]


In [ ]:
# load in hinode files for magnetogram
magincl = fits.open("/content/drive/MyDrive/DATA_LM/SPcubes_20170915_224806_magincl_index.fits")
for frame in range(1, len(magincl)):
    magincl[frame].header['CUNIT1'], magincl[frame].header['CUNIT2'] = 'arcsec', 'arcsec' # change units because they used to be plural which is invalid
MAPSEQ_INCL = sunpy.map.MapSequence([sunpy.map.Map(magincl[frame].data, magincl[frame].header) for frame in range(1, len(magincl))])
magincl.close()

magfld = fits.open("/content/drive/MyDrive/DATA_LM/SPcubes_20170915_224806_magfield_index.fits")
for frame in range(1, len(magfld)):
    magfld[frame].header['CUNIT1'], magfld[frame].header['CUNIT2'] = 'arcsec', 'arcsec' # change units because they used to be plural which is invalid
MAPSEQ_FLD = sunpy.map.MapSequence([sunpy.map.Map(magfld[frame].data, magfld[frame].header) for frame in range(1, len(magfld))])
magfld.close()

In [ ]:
# create aligned map sequence for the magnetogram
ls = []

i = 0
c = 0
while i < len(MAPSEQ_FLD) and c < len(MAPSEQ_CONT_ALIG):
    if (MAPSEQ_CONT_ALIG[c].meta['DATE_OBS'] == MAPSEQ_FLD[i].meta['DATE_OBS']):
        new_data = MAPSEQ_FLD[i].data * np.cos(np.deg2rad(MAPSEQ_INCL[i].data))
        new_map = sunpy.map.Map(new_data, MAPSEQ_FLD[i].meta)
        ls.append(crop(new_map))
        c = c + 1
    else:
        i = i + 1

MAPSEQ_BZ_ALIG = MapSequence(ls)

INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs

INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,d

INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]
INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]
INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]


For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs

INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs

INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of

INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]
INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]
INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]


INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs

INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,d

...

INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]
INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]
INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]
INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]


For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs

INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs

INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of

INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]
INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]
INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]


INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs

INFO:sunpy:Missing metadata for solar radius: assuming the standard radius of the photosphere.
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,dsun_obs,crlt_obs
 [sunpy.map.mapbase]
For frame 'heliographic_stonyhurst' the following metadata is missing: hglt_obs,dsun_obs,hgln_obs
For frame 'heliographic_carrington' the following metadata is missing: crln_obs,d

INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]
INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]
INFO: Missing metadata for solar radius: assuming the standard radius of the photosphere. [sunpy.map.mapbase]


In [ ]:
def fix_map(m):
    new_dat = m.data
    new_dat[new_dat < 0] = 0
    return Map(new_dat, m.meta)

def fix_ms(ms):
    ls = []
    for m in ms:
        ls.append(fix_map(m))
    return MapSequence(ls)

In [ ]:
def convert_fits(mapseq, name):
    hdus = [fits.PrimaryHDU()]

    for i, m in enumerate(mapseq.maps):
        data = m.data
        header = m.meta

        fits_header = fits.Header()

        for key, value in header.items():
            try:
                fits_header[str(key)] = value
            except Exception:
                pass

        hdu = fits.ImageHDU(data=data, header=fits_header, name=f"{name}_{i}")
        hdus.append(hdu)

    fits.HDUList(hdus).writeto(f"/content/drive/MyDrive/DATA_LM/coaligned_data/{name}.fits", overwrite=True)

In [ ]:
def convert_3d_cube(mapseq, name):
    cube = np.stack([m.data for m in mapseq.maps])
    base_header = fits.Header()

    m = mapseq.maps[0]
    for key, value in m.meta.items():
        try:
            base_header[str(key)] = value
        except Exception:
            pass

    base_header['NAXIS'] = 3
    base_header['NAXIS1'] = cube.shape[2]
    base_header['NAXIS2'] = cube.shape[1]
    base_header['NAXIS3'] = cube.shape[0]

    hdu = fits.PrimaryHDU(data=cube, header=base_header)
    hdu.writeto(f"/content/drive/MyDrive/DATA_LM/cube_data/{name}.fits", overwrite=True)

In [ ]:
convert_fits(MAPSEQ_CONT_ALIG, name='cont')
convert_fits(MAPSEQ_BZ_ALIG, name='bz')
convert_fits(MAPSEQ_2832_ALIG, name='2832')
convert_fits(fix_ms(MAPSEQ_2796_ALIG), name='2796')
convert_fits(fix_ms(MAPSEQ_1400_ALIG), name='1400')
convert_fits(fix_ms(MAPSEQ_1330_ALIG), name='1330')

In [ ]:
convert_3d_cube(MAPSEQ_CONT_ALIG, name='cont')
convert_3d_cube(MAPSEQ_BZ_ALIG, name='bz')
convert_3d_cube(MAPSEQ_2832_ALIG, name='2832')
convert_3d_cube(fix_ms(MAPSEQ_2796_ALIG), name='2796')
convert_3d_cube(fix_ms(MAPSEQ_1400_ALIG), name='1400')
convert_3d_cube(fix_ms(MAPSEQ_1330_ALIG), name='1330')